In [4]:
#!pip install -U spacy

In [5]:
#!python -m spacy download en
#!python -m spacy download en_core_web_sm

In [17]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from sqlalchemy import create_engine
import nltk
import spacy
import re

from nltk import sent_tokenize
from nltk import word_tokenize
from nltk.corpus import stopwords
from nltk.stem.snowball import SnowballStemmer
from nltk.stem.wordnet import WordNetLemmatizer

import warnings
warnings.filterwarnings(action="ignore")

#### 1. Apply the data preprocessing techniques you learned here to Cornell Movie--Dialogs Corpus data. You'll be using this dataset when developing a chatbot in a later checkpoint.

In [3]:
postgres_user = 'dsbc_student'
postgres_pw = '7*.8G9QH21'
postgres_host = '142.93.121.174'
postgres_port = '5432'
postgres_db = 'cornell_movie_dialogs'

engine = create_engine('postgresql://{}:{}@{}:{}/{}'.format(
    postgres_user, postgres_pw, postgres_host, postgres_port, postgres_db))

dialogs_df = pd.read_sql_query('select * from dialogs',con=engine)

# no need for an open connection, as we're only doing a single query
engine.dispose()


dialogs_df.head(10)

index                                            dialogs
0      0  Can we make this quick?  Roxanne Korrine and A...
1      1  Well, I thought we'd start with pronunciation,...
2      2  Not the hacking and gagging and spitting part....
3      3  Okay... then how 'bout we try out some French ...
4      4  You're asking me out.  That's so cute. What's ...
5      5                                         Forget it.
6      6  No, no, it's my fault -- we didn't have a prop...
7      7                                           Cameron.
8      8  The thing is, Cameron -- I'm at the mercy of a...
9      9     Seems like she could get a date easy enough...

In [8]:
dialogs_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 304446 entries, 0 to 304445
Data columns (total 2 columns):
 #   Column   Non-Null Count   Dtype 
---  ------   --------------   ----- 
 0   index    304446 non-null  int64 
 1   dialogs  304446 non-null  object
dtypes: int64(1), object(1)
memory usage: 4.6+ MB


In [ ]:
#nlp = spacy.load('en_core_web_sm', disable=['parser', 'ner'])

#nlp.max_length = 20000000
# all the processing work is done below, so it may take a while
#dialogs_doc = nlp(" ".join(dialogs_df.dialogs))


In [10]:
doc = ''
for dialog in dialogs_df['dialogs'][0:20000]:
    doc = doc + ' ' + dialog
doc

' Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again. Well, I thought we\'d start with pronunciation, if that\'s okay with you. Not the hacking and gagging and spitting part.  Please. Okay... then how \'bout we try out some French cuisine.  Saturday?  Night? You\'re asking me out.  That\'s so cute. What\'s your name again? Forget it. No, no, it\'s my fault -- we didn\'t have a proper introduction --- Cameron. The thing is, Cameron -- I\'m at the mercy of a particularly hideous breed of loser.  My sister.  I can\'t date until she does. Seems like she could get a date easy enough... Why? Unsolved mystery.  She used to be really popular when she started high school, then it was just like she got sick of it or something. That\'s a shame. Gosh, if only we could find Kat a boyfriend... Let me see what I can do. C\'esc ma tete. This is my head Right.  See?  You\'re ready for the quiz. I don\'t want to know how t

In [13]:
# remove @ text
doc = re.sub('@[^\s]+','',doc)
doc

' Can we make this quick?  Roxanne Korrine and Andrew Barrett are having an incredibly horrendous public break- up on the quad.  Again. Well, I thought we\'d start with pronunciation, if that\'s okay with you. Not the hacking and gagging and spitting part.  Please. Okay... then how \'bout we try out some French cuisine.  Saturday?  Night? You\'re asking me out.  That\'s so cute. What\'s your name again? Forget it. No, no, it\'s my fault -- we didn\'t have a proper introduction --- Cameron. The thing is, Cameron -- I\'m at the mercy of a particularly hideous breed of loser.  My sister.  I can\'t date until she does. Seems like she could get a date easy enough... Why? Unsolved mystery.  She used to be really popular when she started high school, then it was just like she got sick of it or something. That\'s a shame. Gosh, if only we could find Kat a boyfriend... Let me see what I can do. C\'esc ma tete. This is my head Right.  See?  You\'re ready for the quiz. I don\'t want to know how t

In [18]:
# tokenize
doc_words = word_tokenize(doc)
doc_lower = [word.lower() for word in doc_words]

In [19]:
doc_nostop = [token for token in doc_lower if token not in stopwords.words('english')]

In [21]:
# remove punctuation
doc_nopunc = [word for word in doc_nostop if word.isalpha()]
doc_nopunc

['make',
 'quick',
 'roxanne',
 'korrine',
 'andrew',
 'barrett',
 'incredibly',
 'horrendous',
 'public',
 'quad',
 'well',
 'thought',
 'start',
 'pronunciation',
 'okay',
 'hacking',
 'gagging',
 'spitting',
 'part',
 'please',
 'okay',
 'try',
 'french',
 'cuisine',
 'saturday',
 'night',
 'asking',
 'cute',
 'name',
 'forget',
 'fault',
 'proper',
 'introduction',
 'cameron',
 'thing',
 'cameron',
 'mercy',
 'particularly',
 'hideous',
 'breed',
 'loser',
 'sister',
 'ca',
 'date',
 'seems',
 'like',
 'could',
 'get',
 'date',
 'easy',
 'enough',
 'unsolved',
 'mystery',
 'used',
 'really',
 'popular',
 'started',
 'high',
 'school',
 'like',
 'got',
 'sick',
 'something',
 'shame',
 'gosh',
 'could',
 'find',
 'kat',
 'boyfriend',
 'let',
 'see',
 'tete',
 'head',
 'right',
 'see',
 'ready',
 'quiz',
 'want',
 'know',
 'say',
 'though',
 'want',
 'know',
 'useful',
 'things',
 'like',
 'good',
 'stores',
 'much',
 'champagne',
 'cost',
 'stuff',
 'like',
 'chat',
 'never',
 'life

In [22]:
lemmatizer = WordNetLemmatizer()
doc_lemma = [lemmatizer.lemmatize(word) for word in doc_nopunc]

In [23]:
stemmer = SnowballStemmer('english')
doc_stem = [stemmer.stem(word) for word in doc_lemma]

In [24]:
doc_stem[0:100]

['make',
 'quick',
 'roxann',
 'korrin',
 'andrew',
 'barrett',
 'incred',
 'horrend',
 'public',
 'quad',
 'well',
 'thought',
 'start',
 'pronunci',
 'okay',
 'hack',
 'gag',
 'spit',
 'part',
 'pleas',
 'okay',
 'tri',
 'french',
 'cuisin',
 'saturday',
 'night',
 'ask',
 'cute',
 'name',
 'forget',
 'fault',
 'proper',
 'introduct',
 'cameron',
 'thing',
 'cameron',
 'merci',
 'particular',
 'hideous',
 'breed',
 'loser',
 'sister',
 'ca',
 'date',
 'seem',
 'like',
 'could',
 'get',
 'date',
 'easi',
 'enough',
 'unsolv',
 'mysteri',
 'use',
 'realli',
 'popular',
 'start',
 'high',
 'school',
 'like',
 'got',
 'sick',
 'someth',
 'shame',
 'gosh',
 'could',
 'find',
 'kat',
 'boyfriend',
 'let',
 'see',
 'tete',
 'head',
 'right',
 'see',
 'readi',
 'quiz',
 'want',
 'know',
 'say',
 'though',
 'want',
 'know',
 'use',
 'thing',
 'like',
 'good',
 'store',
 'much',
 'champagn',
 'cost',
 'stuff',
 'like',
 'chat',
 'never',
 'life',
 'point',
 'head',
 'someon',
 'nice']

#### 2. Apply the data preprocessing techniques that you learned here to Twitter US Airline Sentiment data. You'll use this dataset when generating sentences in an upcoming checkpoint.

In [26]:
postgres_user = 'dsbc_student'
postgres_pw = '7*.8G9QH21'
postgres_host = '142.93.121.174'
postgres_port = '5432'
postgres_db = 'twitter_sentiment'

engine = create_engine('postgresql://{}:{}@{}:{}/{}'.format(
    postgres_user, postgres_pw, postgres_host, postgres_port, postgres_db))

twitter_df = pd.read_sql_query('select * from twitter',con=engine)

In [27]:
twitter_df.head()

index            tweet_id airline_sentiment  airline_sentiment_confidence  \
0      0  570306133677760513           neutral                        1.0000   
1      1  570301130888122368          positive                        0.3486   
2      2  570301083672813571           neutral                        0.6837   
3      3  570301031407624196          negative                        1.0000   
4      4  570300817074462722          negative                        1.0000   

  negativereason  negativereason_confidence         airline  \
0           None                        NaN  Virgin America   
1           None                     0.0000  Virgin America   
2           None                        NaN  Virgin America   
3     Bad Flight                     0.7033  Virgin America   
4     Can't Tell                     1.0000  Virgin America   

  airline_sentiment_gold        name negativereason_gold  retweet_count  \
0                   None     cairdin                None              0   
1                   None    jnardino                None              0   
2                   None  yvonnalynn                None              0   
3                   None    jnardino                None              0   
4                   None    jnardino                None              0   

                                                text tweet_coord  \
0                @VirginAmerica What @dhepburn said.        None   
1  @VirginAmerica plus you've added commercials t...        None   
2  @VirginAmerica I didn't today... Must mean I n...        None   
3  @VirginAmerica it's really aggressive to blast...        None   
4  @VirginAmerica and it's a really big bad thing...        None   

               tweet_created tweet_location               user_timezone  
0  2015-02-24 11:35:52 -0800           None  Eastern Time (US & Canada)  
1  2015-02-24 11:15:59 -0800           None  Pacific Time (US & Canada)  
2  2015-02-24 11:15:48 -0800      Lets Play  Central Time (US & Canada)  
3  2015-02-24 11:15:36 -0800           None  Pacific Time (US & Canada)  
4  2015-02-24 11:14:45 -0800           None  Pacific Time (US & Canada)

In [28]:
doc = ''
for text in twitter_df['text']:
    doc = doc + ' ' + text
doc

' @VirginAmerica What @dhepburn said. @VirginAmerica plus you\'ve added commercials to the experience... tacky. @VirginAmerica I didn\'t today... Must mean I need to take another trip! @VirginAmerica it\'s really aggressive to blast obnoxious "entertainment" in your guests\' faces &amp; they have little recourse @VirginAmerica and it\'s a really big bad thing about it @VirginAmerica seriously would pay $30 a flight for seats that didn\'t have this playing.\nit\'s really the only bad thing about flying VA @VirginAmerica yes, nearly every time I fly VX this “ear worm” won’t go away :) @VirginAmerica Really missed a prime opportunity for Men Without Hats parody, there. https://t.co/mWpG7grEZP @virginamerica Well, I didn\'t…but NOW I DO! :-D @VirginAmerica it was amazing, and arrived an hour early. You\'re too good to me. @VirginAmerica did you know that suicide is the second leading cause of death among teens 10-24 @VirginAmerica I &lt;3 pretty graphics. so much better than minimal iconog

In [29]:
# remove @ text
doc = re.sub('@[^\s]+','',doc)
doc

'  What  said.  plus you\'ve added commercials to the experience... tacky.  I didn\'t today... Must mean I need to take another trip!  it\'s really aggressive to blast obnoxious "entertainment" in your guests\' faces &amp; they have little recourse  and it\'s a really big bad thing about it  seriously would pay $30 a flight for seats that didn\'t have this playing.\nit\'s really the only bad thing about flying VA  yes, nearly every time I fly VX this “ear worm” won’t go away :)  Really missed a prime opportunity for Men Without Hats parody, there. https://t.co/mWpG7grEZP  Well, I didn\'t…but NOW I DO! :-D  it was amazing, and arrived an hour early. You\'re too good to me.  did you know that suicide is the second leading cause of death among teens 10-24  I &lt;3 pretty graphics. so much better than minimal iconography. :D  This is such a great deal! Already thinking about my 2nd trip to  &amp; I haven\'t even gone on my 1st trip yet! ;p   I\'m flying your #fabulous #Seductive skies agai

In [30]:
# tokenize
doc_words = word_tokenize(doc)
# lowercase
doc_lower = [word.lower() for word in doc_words]
doc_nostop = [token for token in doc_lower if token not in stopwords.words('english')]
# remove punctuation
doc_nopunc = [word for word in doc_nostop if word.isalpha()]

In [31]:
lemmatizer = WordNetLemmatizer()
doc_lemma = [lemmatizer.lemmatize(word) for word in doc_nopunc]

stemmer = SnowballStemmer('english')
doc_stem = [stemmer.stem(word) for word in doc_lemma]
doc_stem[0:100]

['said',
 'plus',
 'ad',
 'commerci',
 'experi',
 'tacki',
 'today',
 'must',
 'mean',
 'need',
 'take',
 'anoth',
 'trip',
 'realli',
 'aggress',
 'blast',
 'obnoxi',
 'entertain',
 'guest',
 'face',
 'amp',
 'littl',
 'recours',
 'realli',
 'big',
 'bad',
 'thing',
 'serious',
 'would',
 'pay',
 'flight',
 'seat',
 'play',
 'realli',
 'bad',
 'thing',
 'fli',
 'va',
 'yes',
 'near',
 'everi',
 'time',
 'fli',
 'vx',
 'ear',
 'worm',
 'go',
 'away',
 'realli',
 'miss',
 'prime',
 'opportun',
 'men',
 'without',
 'hat',
 'parodi',
 'http',
 'well',
 'amaz',
 'arriv',
 'hour',
 'earli',
 'good',
 'know',
 'suicid',
 'second',
 'lead',
 'caus',
 'death',
 'among',
 'teen',
 'lt',
 'pretti',
 'graphic',
 'much',
 'better',
 'minim',
 'iconographi',
 'great',
 'deal',
 'alreadi',
 'think',
 'trip',
 'amp',
 'even',
 'gone',
 'trip',
 'yet',
 'p',
 'fli',
 'fabul',
 'seduct',
 'sky',
 'u',
 'take',
 'stress',
 'away',
 'travel',
 'http',
 'thank']